In [2]:
#  sentence_transformers import SentenceTransformer, InputExample, losses
from torch.utils.data import DataLoader
from sklearn.metrics import classification_report
from sklearn.metrics.pairwise import cosine_similarity
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import TfidfVectorizer
import logging
from sentence_transformers import SentenceTransformer
import re
import string
import nltk
from nltk.corpus import stopwords
stop_words = set(stopwords.words('english'))
logging.basicConfig(format='%(asctime)s - %(message)s', level=logging.INFO)

/Users/sarahpopeck/anaconda3/lib/python3.11/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


In [10]:
# Load datasets
df_train = pd.read_csv("train_balanced_25k.csv")
df_train = df_train.dropna(subset=['query', 'full_product_text']).reset_index(drop=True)

df_test = pd.read_csv("test_4k_nonoverlap.csv")
df_test = df_test.dropna(subset=['query', 'full_product_text']).reset_index(drop=True)

# Extract values
queries = df_test['query'].tolist()
true_product_ids = df_test['product_id'].tolist()
products = df_train['full_product_text'].tolist()
product_ids = df_train['product_id'].tolist()

## Model 1: TF-IDF

In [11]:
# Filter to Training dataset with Relevant (E) Labels
sample_df = df_train[
    (df_train["esci_label"] == "E")]

# Extract queries and product titles
queries = sample_df['query'].astype(str).values
products = sample_df['product_title'].astype(str).values

# TF-IDF Vectorizer on combined
vectorizer = TfidfVectorizer()
query_vecs = vectorizer.fit_transform(queries)
product_vecs = vectorizer.transform(products)  # Use same vocab

# Score and Recommend Top 3 Products per Query
for i, query in enumerate(queries):
    scores = cosine_similarity(query_vecs[i], product_vecs).flatten()
    ranked_indices = scores.argsort()[::-1]
    
    print(f"\nTop matches for: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {products[idx]} (score: {scores[idx]:.4f})")


Top matches for: 'columbia womens coat'
- Columbia Men's Glennaker Lake Front-Zip Jacket, Columbia Grey/Boulder, X-Large (score: 0.4687)
- Columbia Men's RFID Passcase Wallet (score: 0.3637)
- Columbia Women's Kruser Ridge II Softshell, Black, Medium (score: 0.3583)

Top matches for: 'black tights'
- DKNY Super Opaque Control Top Tights, Medium, Black (score: 0.5627)
- VERO MONTE 2 Pairs Womens Opaque Warm Fleece Lined Tights (BLACK) 46031 (score: 0.4839)
- adidas womens Believe This Solid 7/8 Tights Black 3X (score: 0.4790)

Top matches for: 'mounted wall shelf with drawers'
- WELLAND White Finished 48 inch Pine Wood Fireplace Mantel Shelf Wall Mounted,Corona Crown Molding Floating Wall Picture Ledge Shelves (score: 0.4293)
- Americanflat 12x18 Poster Frame in White - Composite Wood with Shatter Resistant Glass - Wall Mounted Horizontal and Vertical Formats (score: 0.3976)
- YOHOM White Floating Shelf Adhesive Bathroom Wall Storage Shelf No Drilling Display Ledge Shelf Organizer for 


Top matches for: 'lighted electrical outlet cover'
- 100-Feet 3 Outlet Extension Cord, Kasonic UL Listed, 16/3 SJTW 3-Wire Grounded, 10 Amp 125 V 1625 Watts, Multi-Outlet Indoor/Outdoor Use (score: 0.2824)
- DEWENWILS Outdoor Light Timer Waterproof, Plug in Sensor Outlet Timer Switch, 100 ft Range Remote Control with 2 Grounded Electrical Outlets for Yard Landscape Holiday Light, 15A 1/2HP UL Listed (score: 0.2301)
- Gratury Junction Box, Hinged Cover Stainless Steel Clip IP67 Waterproof Plastic Enclosure for Electrical Project Includes Mounting Plate and Wall Bracket 390×290×180mm (15.3"×11.4"×7.1") (score: 0.2207)

Top matches for: '10x16.5 skid steer tires without rum'
- Skid Steer - Truck Tunes for Kids (score: 0.4806)
- Bruder 02482 Caterpillar Skid Steer Loader (score: 0.4792)
- Air-Loc 10-16.5 Premium Radial Tire Inner Tube Industrial Skid Steer Bobcat 10. 00-16. 5 (score: 0.2406)

Top matches for: 'arctic king 7 cu ft chest freezer, black'
- Arctic King 7.0 cu ft Chest Freezer


Top matches for: 'high wasted tights women'
- Black & White Checker Thigh-High Halloween Adult Women's Cosplay Costume Tights (score: 0.3834)
- CozyWow Women's Solid Color Soft Semi Opaque Footed Tights Pantyhose Coffee (score: 0.2957)
- VIISHOW Tiktok Leggings High Waist Yoga Pants for Women, Booty Bubble Butt Lifting Workout Running Tights, White, Small (score: 0.2942)

Top matches for: 'sipsnap'
- 23.62" Extended Flexible Crevice Tool for Vacuum Cleaner Hose 1.25 inch 32mm Replace Crevice Flat Nozzle Tool Vacuum Accessories Fit Most Space Cleaning (score: 0.0000)
- SwimSchool Baby Splash Play Mat Seat, Inflatable Pool for Babies & Infants with Backrest and Canopy, Includes Three Stackable Ring Baby Water Toys (SSI11261Z) (score: 0.0000)
- Woplagyreat Kids Face Mask with Adjustable Ear Loops, Cute Pineapple Fabric Washable Reusable Cover, Designer Breathable Madks Facemask for Girl Boy Children Gift (score: 0.0000)

Top matches for: 'white and blue men soccer cleats'
- DREAM PAIRS B


Top matches for: 'breville barista touch'
- Breville BES880BSS Barista Touch Espresso Machine, Brushed Stainless Steel (score: 0.6613)
- Breville BES880BSS Barista Touch Espresso Machine, Brushed Stainless Steel (score: 0.6613)
- Touch The Wall (score: 0.3306)

Top matches for: 'womens 3mm surf wetsuit'
- Women Shorty Wetsuit 3mm Long Sleeve Neoprene Diving Suit Thermal Swimsuit Back Zip for Water Sports Kayakboarding Surfing Snorkeling (Navy, M) (score: 0.3708)
- Kanu Surf Miles Swim Trunks (Regular & Extended Sizes), Surf Camo Black, XX-Large (score: 0.3017)
- Rip Curl Men's Wetty Surf Hat, Black, 1SZ (score: 0.3014)

Top matches for: 'oculus quest'
- Aenllosi Hard Carrying Case Compatible with Oculus Quest 2 & Quest VR Gaming Headset (Black) (score: 0.6637)
- Oculus Quest All-in-one VR Gaming Headset – 128GB (UK Import) (score: 0.5751)
- Oculus Quest 2 — Advanced All-In-One Virtual Reality Headset — 256 GB (score: 0.5118)

Top matches for: 'cute iphone 6s case'
- iPhone 6s 6 Case w


Top matches for: 'superhero learning games'
- Learning Pad / Kids Phone with 6 Toddler Learning Games. Touch and Learn Toddler Tablet for Numbers, ABC and Words Learning. Educational Learning Toys for Boys and Girls - 3 Year Old (score: 0.4787)
- Mockingjay: The Hunger Games, Book 3 (score: 0.3288)
- Babe Rock Wooden Color Sorting Stacking Rings Board Educational Learning Counting Toys Puzzle Games for 1 Year Old Preschool Kids Children Gift (score: 0.2882)

Top matches for: 'lysa terkeurst books it wasnt'
- It's Summer! It's Camp! It's Vanguard! (score: 0.3263)
- It's Not Me, It's You (score: 0.2891)
- It's Not Me, It's You (Young In Love Book 1) (score: 0.2246)

Top matches for: 'matte texture clay'
- Hair Clay For Men | Smooth Viking Clay Pomade for Matte Finish & Strong Hold (2 Ounces) - Non-Greasy & Shine-Free Hair Styling Clay - Mineral Oil Free Mens Hair Product (score: 0.4137)
- 50 Colors Polymer Clay, Modeling Clay with 29 Clay Tools and Accessories, Starter Kit Clay for Kids

...


Top matches for: 'baby side sleeping positioner'
- KAKIBLIN Baby Bed Mattress, Baby Protective Pillow Baby Sleeping Pad Bassinet Mattress Pad for Newborn Baby and Infant Age 0-12 Months, Blue (score: 0.3240)
- Ascoli ASBS2100EW 20.6 Cu. Ft. Side by Side Refrigerator - White (score: 0.3085)
- Baby Handprint and Footprint Kit | Keepsake For Newborn Boys & Girls, Baby Girl Gifts & Baby Boy Gifts, New Mom Baby Shower Gifts, Baby Milestone Picture Frames Baby Registry, Nursery Decor (score: 0.2616)

Top matches for: 'newborn girl jeans set'
- Spitfire Girl (score: 0.4807)
- 8 piece Layette Baby Doll Gift Set | JC Toys - La Newborn Nursery | 14" Life-Like Newborn Doll w/ Accessories | Pink | Ages 2+ (score: 0.3281)
- Carter's Baby Girls' 6-Piece Jacket and Vest Set, Denim Quilted/Pink Dot, Newborn (score: 0.2823)

Top matches for: 'navy 3inch running shorfs'
- Brentwood 557 Corduroy Bedrest, Navy (score: 0.2592)
- U.S. Air Force Long Sleeve T-Shirt. Navy Blue (Large, Navy Blue) (score: 0.24


Top matches for: 'a series samsung'
- Alapmk Protective Case Cover for 11.6" Samsung Chromebook 4 XE310XBA & Chromebook 3 XE500C13 & Chromebook 2 XE503C12 XE500C12 Laptop(Note:Not fit Samsung XE303C12 Series Chromebook),Love Tree (score: 0.5080)
- Playboy (The Playboy Series Book 1) (score: 0.4411)
- TIMTU Compatible with Apple Watch Band 44mm 42mm, for Women Men, Silicone Sport Band Compatible with iWatch Series 3, Series 4, Series 2, Series 1, M/L White/Black (score: 0.4374)

Top matches for: 'white throw pillow'
- Alex Orthopedic - Cervical Neck Roll Pillow Case Only, Bolster Pillow Cover - Pillow Case for Cervical Pillow, Round Neck Pillow, Bolster Pillow for Bed, Log Pillow- Beige Satin - Set of Two (score: 0.4895)
- Edow Throw Pillow Insert, Set of 2 Down Alternative Polyester Square Form Decorative Pillow, Cushion,Sham Stuffer. (White, 20x20) (score: 0.4760)
- Home Brilliant Christmas Pillow Covers 18x18 Red Throw Pillow Covers Farmhouse Decorative Boho Decoration Throw Pillows


Top matches for: 'xl tall moisture wicking shirt'
- Champion Mens Big & Tall Active T Shirt Moisture Wicking Black 3X (score: 0.5933)
- Columbia Women’s PFG Lo Drag Long Sleeve Shirt, Moisture Wicking, Sun Protection White, XX-Large (score: 0.4295)
- frueo Men's 3 Pack Running Shirts Dry Fit Moisture Wicking Short Sleeve Mesh Workout Training T-Shirts,Black Gray Green,XL (score: 0.4251)

Top matches for: 'fnaf mascot costume'
- Smiffys Ginger Power, 1990s Icon Costume (score: 0.2909)
- Rubie's Costume Five Nights at Freddy's Tween Bonnie Costume Set (score: 0.2518)
- Official Louisiana State 'LSU' Tiger Mascot NCCA College Logo Iron On Patch (score: 0.2444)

Top matches for: 'gaming wifi routers for home'
- Speedefy AC2100 Smart WiFi Router - Dual Band Gigabit Wireless Router for Home & Gaming, 4x4 MU-MIMO, 7x6dBi External Antennas for Strong Signal, Parental Control, Support IPv6 (Model K7) (score: 0.3003)
- CyberpowerPC Gamer Xtreme VR Gaming PC, Intel Core i5-9400F 2.9GHz, NVIDIA G


Top matches for: 'shower mat without suction cups for textured tub surface'
- European Coatings Non Slip Bath Mat NO Suction Cups for Refinished Reglazed Tub 41" x 15" Clear (score: 0.4393)
- Yolife Non Slip Bath Mat Quick Drain Shower Floor Mat Colorful Bathtub Mat Slatted Duckboard Design with Suction Cups for Bathroom Hotel Gym Kitchen | Easy Dry| Non-Toxic, BPA, Latex, Phthalate Free (score: 0.3234)
- SPRI Xerball Medicine Ball Thick Walled Durable Construction with Textured Surface, Yellow, 2-Pound (score: 0.3134)

Top matches for: 'the block hot'
- BLOCK HOT Pt 2 [Explicit] (score: 0.8904)
- Block Hot [Explicit] (score: 0.8904)
- Block Hot [Explicit] (score: 0.8904)

Top matches for: 'mickey mouse waffle maker'
- Mickey Waffle Maker (score: 0.9027)
- 3 Minnie Mouse Black Red Pink Silver Bow-Mickey Mouse Ears Headband Costume (score: 0.4008)
- LEGO DUPLO l Disney Mickey Mouse Clubhouse Mickey & Minnie Birthday Parade 10597 Disney Toy (24 Pieces) (score: 0.3996)

Top matches for: 

KeyboardInterrupt: 

## Model 2: SentenceTransformer

In [ ]:
# Sample train data and construct product text
train_df = df_train.sample(n=10000, random_state=42).copy()
train_products = train_df['full_product_text'].astype(str).tolist()
train_titles = train_df['product_title'].astype(str).tolist()  # for display

# Prepare queries
test_queries = train_df['query'].astype(str).tolist()

# Load the model and compute embeddings
model = SentenceTransformer('all-MiniLM-L6-v2')
product_vecs = model.encode(train_products, convert_to_numpy=True)
query_vecs = model.encode(test_queries, convert_to_numpy=True)

# Recommend top-3 products for each test query
for i, query in enumerate(test_queries):
    scores = cosine_similarity(query_vecs[i].reshape(1, -1), product_vecs).flatten()
    
    # Normalize scores between 0 and 1
    scores = (scores - scores.min()) / (scores.max() - scores.min() + 1e-8)
    ranked_indices = scores.argsort()[::-1]

    print(f"\nTop matches for test query: '{query}'")
    for idx in ranked_indices[:3]:
        print(f"- {train_titles[idx]} (score: {scores[idx]:.4f})")


2025-08-01 17:12:59,979 - Use pytorch device_name: mps
2025-08-01 17:12:59,980 - Load pretrained SentenceTransformer: all-MiniLM-L6-v2
/Users/sarahpopeck/anaconda3/lib/python3.11/site-packages/huggingface_hub/file_download.py:943: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Batches:   0%|          | 0/313 [00:00<?, ?it/s]

## Model 3: SentenceTransformer + Preprocessing

In [ ]:
import pandas as pd
import re
import string
from sklearn.metrics.pairwise import cosine_similarity
from sentence_transformers import SentenceTransformer
from nltk.corpus import stopwords

# Make sure to download stopwords if not already
import nltk
nltk.download('stopwords')

stop_words = set(stopwords.words('english'))

# Preprocessing function
def preprocess(text):
    text = text.lower()
    text = text.translate(str.maketrans('', '', string.punctuation))
    text = re.sub(r'\d+', '', text)
    tokens = text.split()
    filtered = [word for word in tokens if word not in stop_words]
    return ' '.join(filtered)

# Preprocess the product descriptions
df_train_preprocess = df_train.copy()
df_train_preprocess['full_product_text'] = df_train_preprocess['full_product_text'].astype(str).apply(preprocess)
train_products_pre = df_train_preprocess['full_product_text'].tolist()  # This is now used for encoding

# Also keep track of product titles to show as recommendations
train_titles = df_train_preprocess['product_title'].astype(str).tolist()

# Preprocess and prepare test queries
df_test_preprocess = df_test.copy()
df_test_preprocess['query'] = df_test_preprocess['query'].astype(str).apply(preprocess)
test_queries = df_test_preprocess['query'].tolist()

# Load model and encode text
model = SentenceTransformer('all-MiniLM-L6-v2')
product_vecs = model.encode(train_products_pre, convert_to_numpy=True)
query_vecs = model.encode(test_queries, convert_to_numpy=True)

# Recommend top-3 products for each test query
for i, query in enumerate(test_queries):
    scores = cosine_similarity(query_vecs[i].reshape(1, -1), product_vecs).flatten()
    
    # Normalize scores to [0, 1]
    scores = (scores - scores.min()) / (scores.max() - scores.min() + 1e-8)
    ranked_indices = scores.argsort()[::-1]

    print(f"\nTop matches for test query: '{df_test['query'].iloc[i]}'")
    for idx in ranked_indices[:3]:
        print(f"- {train_titles[idx]} (score: {scores[idx]:.4f})")


In [ ]:
# Custom ESCI Scoring
esci_points = {'E': 3, 'C': 2, 'S': 1, 'I': 0}
total_possible = 0
total_achieved = 0

# Evaluate test set differently
for i, row in df_test.iterrows():
    query = row['query']
    true_product = row['product_title']
    true_label = row['esci_label']

    query_vec = model.encode([query], convert_to_numpy=True)
    scores = cosine_similarity(query_vec, product_vecs).flatten()
    scores = (scores - scores.min()) / (scores.max() - scores.min() + 1e-8)
    ranked_indices = scores.argsort()[::-1][:3]

    print(f"\n🔍 Top matches for query: '{row['query']}'")
    matched = False
    for rank, idx in enumerate(ranked_indices, start=1):
        predicted_title = train_titles[idx]
        print(f"{rank}. {predicted_title} (score: {scores[idx]:.4f})")
        if predicted_title.strip().lower() == true_product.strip().lower() and not matched:
            point_value = esci_points.get(true_label, 0)
            total_achieved += point_value
            matched = True
            print(f"✅ Match found with label '{true_label}' (+{point_value} points)")

    total_possible += esci_points.get(true_label, 0)

# Final Score
print(f"\n🌟 Total Achieved Points: {total_achieved}")
print(f"🎯 Total Possible Points: {total_possible}")
if total_possible > 0:
    print(f"📊 ESCI-Based Retrieval Score: {total_achieved / total_possible:.4f}")
else:
    print("⚠️ No valid labels found in test set.")
